In [3]:
# Install required libraries (if not already installed)
!pip install folium pandas numpy branca

# Import necessary libraries
import folium
import pandas as pd
import numpy as np
from folium.plugins import MarkerCluster

# Load the dataset
file_path = "geocoded_addresses_google.csv"  # Update with your actual file
df = pd.read_csv(file_path)

# Drop rows with missing coordinates or rent values
df = df.dropna(subset=["latitude", "longitude", 
                        "Rental price (per month) BEFORE the increase (put N/A if FMR)", 
                        "Rental price (per month) AFTER the increase"])

# Remove "$" and "," and extract only numeric values using regex
df["rent_before"] = df["Rental price (per month) BEFORE the increase (put N/A if FMR)"].str.replace("[^\d.]", "", regex=True)
df["rent_after"] = df["Rental price (per month) AFTER the increase"].str.replace("[^\d.]", "", regex=True)

# Convert to numeric, setting errors='coerce' to handle non-numeric values
df["rent_before"] = pd.to_numeric(df["rent_before"], errors="coerce")
df["rent_after"] = pd.to_numeric(df["rent_after"], errors="coerce")

# Drop rows where conversion failed (rows that had text instead of numbers)
df = df.dropna(subset=["rent_before", "rent_after"])

# Calculate percentage increase in rent
df["percent_increase"] = ((df["rent_after"] - df["rent_before"]) / df["rent_before"]) * 100

# Define color categories for rent increase
def get_color(percent):
    if percent <= 10:
        return "#00ff00"  # Green
    elif percent <= 20:
        return "#aaff00"  # Yellow-Green
    elif percent <= 30:
        return "#ffaa00"  # Orange
    elif percent <= 40:
        return "#ff5500"  # Dark Orange
    elif percent <= 50:
        return "#ff2200"  # Red-Orange
    else:
        return "#cc0000"  # Dark Red

# Initialize the map centered on Los Angeles
m = folium.Map(location=[34.0522, -118.2437], zoom_start=10, tiles="cartodbpositron")  # Light gray basemap

# Create a marker cluster for better visualization
marker_cluster = MarkerCluster().add_to(m)

# Add each rental as a colored point
for _, row in df.iterrows():
    popup_info = f"""
    <b>Address:</b> {row['Address - House number, street, and apartment number']}<br>
    <b>City:</b> {row['City']}, {row['State']} {row['ZIP']}<br>
    <b>Rent Before:</b> ${row['rent_before']:,.2f}<br>
    <b>Rent After:</b> ${row['rent_after']:,.2f}<br>
    <b>Percent Increase:</b> {row['percent_increase']:.2f}%
    """
    
    folium.CircleMarker(
        location=[row["latitude"], row["longitude"]],
        radius=6,  # Marker size
        color=get_color(row["percent_increase"]),
        fill=True,
        fill_color=get_color(row["percent_increase"]),
        fill_opacity=0.9,
        popup=folium.Popup(popup_info, max_width=300)
    ).add_to(marker_cluster)

# Define the legend's HTML and CSS
legend_html = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed; 
    bottom: 40px; left: 40px; width: 250px; height: 210px;  
    background-color: white; z-index:9999; font-size:14px;
    border-radius: 8px; padding: 12px; box-shadow: 2px 2px 5px rgba(0,0,0,0.3);
    font-family: Arial, sans-serif;
">
    <b>📍 Rent Increase Severity</b><br>
    <small>(% increase in rent)</small><br><br>
    <i style="background:#00ff00;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> ≤ 10%<br>
    <i style="background:#aaff00;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 11 - 20%<br>
    <i style="background:#ffaa00;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 21 - 30%<br>
    <i style="background:#ff5500;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 31 - 40%<br>
    <i style="background:#ff2200;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 41 - 50%<br>
    <i style="background:#cc0000;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 51% +<br>
</div>
{% endmacro %}
"""

# Inject the legend into the map
from branca.element import Template, MacroElement
legend = MacroElement()
legend._template = Template(legend_html)
m.get_root().html.add_child(legend)

# Save and display the interactive map
m.save("interactive_rent_increase_map.html")
m


In [4]:
# Install required libraries (if not already installed)
!pip install folium pandas numpy branca

# Import necessary libraries
import folium
import pandas as pd
import numpy as np
from folium.plugins import MarkerCluster

# Load the dataset
file_path = "geocoded_addresses_google.csv"  # Update with your actual file
df = pd.read_csv(file_path)

# Drop rows with missing coordinates or rent values
df = df.dropna(subset=["latitude", "longitude", 
                        "Rental price (per month) BEFORE the increase (put N/A if FMR)", 
                        "Rental price (per month) AFTER the increase"])

# Remove "$" and "," and extract only numeric values using regex
df["rent_before"] = df["Rental price (per month) BEFORE the increase (put N/A if FMR)"].str.replace("[^\d.]", "", regex=True)
df["rent_after"] = df["Rental price (per month) AFTER the increase"].str.replace("[^\d.]", "", regex=True)

# Convert to numeric, setting errors='coerce' to handle non-numeric values
df["rent_before"] = pd.to_numeric(df["rent_before"], errors="coerce")
df["rent_after"] = pd.to_numeric(df["rent_after"], errors="coerce")

# Drop rows where conversion failed (rows that had text instead of numbers)
df = df.dropna(subset=["rent_before", "rent_after"])

# Calculate percentage increase in rent
df["percent_increase"] = ((df["rent_after"] - df["rent_before"]) / df["rent_before"]) * 100

# Define color categories for rent increase
def get_color(percent):
    if percent <= 10:
        return "#00ff00"  # Green
    elif percent <= 20:
        return "#aaff00"  # Yellow-Green
    elif percent <= 30:
        return "#ffaa00"  # Orange
    elif percent <= 40:
        return "#ff5500"  # Dark Orange
    elif percent <= 50:
        return "#ff2200"  # Red-Orange
    else:
        return "#cc0000"  # Dark Red

# Initialize the map centered on Los Angeles
m = folium.Map(location=[34.0522, -118.2437], zoom_start=10, tiles="cartodbpositron")  # Light gray basemap

# Create a marker cluster for better visualization
marker_cluster = MarkerCluster().add_to(m)

# Add each rental as a colored point
for _, row in df.iterrows():
    popup_info = f"""
    <b>Address:</b> {row['Address - House number, street, and apartment number']}<br>
    <b>City:</b> {row['City']}, {row['State']} {row['ZIP']}<br>
    <b>Rent Before:</b> ${row['rent_before']:,.2f}<br>
    <b>Rent After:</b> ${row['rent_after']:,.2f}<br>
    <b>Percent Increase:</b> {row['percent_increase']:.2f}%
    """
    
    folium.CircleMarker(
        location=[row["latitude"], row["longitude"]],
        radius=6,  # Marker size
        color=get_color(row["percent_increase"]),
        fill=True,
        fill_color=get_color(row["percent_increase"]),
        fill_opacity=0.9,
        popup=folium.Popup(popup_info, max_width=300)
    ).add_to(marker_cluster)

# Define the legend's HTML and CSS
from branca.element import Template, MacroElement

# Updated legend HTML with a larger height for better rendering
legend_html = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed; 
    bottom: 40px; left: 40px; width: 270px; height: 220px;  
    background-color: white; z-index:9999; font-size:14px;
    border-radius: 8px; padding: 15px; box-shadow: 2px 2px 5px rgba(0,0,0,0.3);
    font-family: Arial, sans-serif;
">
    <b>📍 Rent Increase Severity</b><br>
    <small>(% increase in rent)</small><br><br>
    <i style="background:#00ff00;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> ≤ 10%<br>
    <i style="background:#aaff00;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 11 - 20%<br>
    <i style="background:#ffaa00;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 21 - 30%<br>
    <i style="background:#ff5500;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 31 - 40%<br>
    <i style="background:#ff2200;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 41 - 50%<br>
    <i style="background:#cc0000;width:15px;height:15px;display:inline-block; margin-right: 8px;"></i> 51% +<br>
</div>
{% endmacro %}
"""

# Inject the legend correctly
legend = MacroElement()
legend._template = Template(legend_html)
m.get_root().html.add_child(legend)

# Save the updated map
m.save("interactive_rent_increase_map.html")


# Inject the legend into the map
from branca.element import Template, MacroElement
legend = MacroElement()
legend._template = Template(legend_html)
m.get_root().html.add_child(legend)

# Save and display the interactive map
m.save("interactive_rent_increase_map.html")
m
